cnn_mnist.py

In [2]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    # Reshape X to 4-D tensor: [batch_size, width, height, channels]
    # MNIST images are 28x28 pixels, and have one color channel
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    # Computes 32 features using a 5x5 filter with ReLU activation.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 28, 28, 1]
    # Output Tensor Shape: [batch_size, 28, 28, 32]
    conv1 = tf.layers.conv2d(
            inputs=input_layer,
            filters=32,
            kernel_size=[5, 5],
            padding="same",
            activation=tf.nn.relu)

    # Pooling Layer #1
    # First max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 28, 28, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 32]
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2
    # Computes 64 features using a 5x5 filter.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 14, 14, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 64]
    conv2 = tf.layers.conv2d(
            inputs=pool1,
            filters=64,
            kernel_size=[5, 5],
            padding="same",
            activation=tf.nn.relu)

    # Pooling Layer #2
    # Second max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 14, 14, 64]
    # Output Tensor Shape: [batch_size, 7, 7, 64]
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Flatten tensor into a batch of vectors
    # Input Tensor Shape: [batch_size, 7, 7, 64]
    # Output Tensor Shape: [batch_size, 7 * 7 * 64]
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

    # Dense Layer
    # Densely connected layer with 1024 neurons
    # Input Tensor Shape: [batch_size, 7 * 7 * 64]
    # Output Tensor Shape: [batch_size, 1024]
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

    # Add dropout operation; 0.6 probability that element will be kept
    dropout = tf.layers.dropout(
            inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits layer
    # Input Tensor Shape: [batch_size, 1024]
    # Output Tensor Shape: [batch_size, 10]
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
            # Generate predictions (for PREDICT and EVAL mode)
            "classes": tf.argmax(input=logits, axis=1),
            # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
            # `logging_hook`.
            "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
                loss=loss,
                global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
            "accuracy": tf.metrics.accuracy(
                    labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
            mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
    # Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images    # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images    # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
            model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

    # Set up logging for predictions
    # Log the values in the "Softmax" tensor with label "probabilities"
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(
            tensors=tensors_to_log, every_n_iter=50)

    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
            x={"x": train_data},
            y=train_labels,
            batch_size=100,
            num_epochs=None,
            shuffle=True)
    mnist_classifier.train(
            input_fn=train_input_fn,
            steps=20000,
            hooks=[logging_hook])

    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
            x={"x": eval_data},
            y=eval_labels,
            num_epochs=1,
            shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)


if __name__ == "__main__":
    tf.app.run()

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f3b48e0fc50>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensor

INFO:tensorflow:loss = 2.2846885, step = 2
INFO:tensorflow:probabilities = [[0.1012914  0.10509696 0.08603057 0.09227894 0.09504215 0.08611804
  0.11254121 0.09783058 0.11753689 0.10623327]
 [0.09885275 0.10155702 0.0913178  0.10720126 0.09112876 0.1012763
  0.11610016 0.08792283 0.10315108 0.10149202]
 [0.08852315 0.12265972 0.08384664 0.0985488  0.08854954 0.09354883
  0.11803471 0.0963262  0.1079859  0.10197648]
 [0.1148044  0.09829732 0.08600342 0.10474145 0.09285832 0.10487396
  0.1077899  0.09318027 0.10374132 0.09370963]
 [0.09557445 0.10323479 0.08728827 0.10777076 0.09104745 0.09876465
  0.11397    0.09852255 0.10729274 0.09653439]
 [0.10216558 0.10313977 0.087345   0.09886505 0.11529807 0.08514927
  0.10930566 0.08877782 0.10025594 0.1096978 ]
 [0.10413145 0.10586855 0.089159   0.1012798  0.08697601 0.09703612
  0.11405947 0.09811479 0.10848691 0.09488788]
 [0.09656647 0.094018   0.0922766  0.09165364 0.09363133 0.09651785
  0.12067867 0.0996096  0.10369173 0.11135615]
 [0.10

INFO:tensorflow:global_step/sec: 7.31663
INFO:tensorflow:probabilities = [[0.09888991 0.10377673 0.09057528 0.11092869 0.09502386 0.08396338
  0.11385191 0.0995502  0.09731591 0.10612418]
 [0.09435028 0.10667063 0.09132253 0.09945277 0.10060839 0.09039965
  0.11365537 0.0948569  0.10504917 0.10363431]
 [0.09936857 0.09929857 0.08244164 0.10956132 0.1000817  0.10082881
  0.11335471 0.09328832 0.09850029 0.10327604]
 [0.10571479 0.10487375 0.08821022 0.09095114 0.09856584 0.09464771
  0.11393992 0.10190969 0.09401763 0.10716926]
 [0.10240851 0.10480227 0.09098514 0.09972686 0.0977973  0.10272196
  0.09751196 0.09949891 0.10379297 0.10075407]
 [0.09832715 0.10091937 0.09386984 0.10830957 0.09340928 0.09865529
  0.10576903 0.10653277 0.1029737  0.09123397]
 [0.10203715 0.11341299 0.08147988 0.0963655  0.10668983 0.0931007
  0.10925645 0.09709629 0.10227784 0.09828345]
 [0.09546068 0.09779163 0.0958132  0.0992367  0.10224085 0.09302641
  0.12205914 0.08799724 0.09795596 0.10841817]
 [0.0998

INFO:tensorflow:loss = 2.288739, step = 102 (13.669 sec)
INFO:tensorflow:probabilities = [[0.10130785 0.10333233 0.08855326 0.09398231 0.10595786 0.09331029
  0.1135941  0.09796546 0.09796736 0.10402919]
 [0.10520991 0.10152398 0.08662216 0.09474372 0.10093378 0.08779061
  0.11480969 0.09367744 0.10942518 0.10526346]
 [0.10068545 0.10089903 0.09182216 0.09482572 0.10182148 0.08876863
  0.10755682 0.09235314 0.10859217 0.11267538]
 [0.10584383 0.09721223 0.07738668 0.10222317 0.09937047 0.08288191
  0.12202035 0.09593841 0.1095478  0.10757507]
 [0.10749233 0.10424716 0.08069793 0.1078808  0.09868526 0.09696209
  0.10998792 0.09086172 0.10296217 0.10022272]
 [0.09935975 0.10147762 0.09159455 0.10002558 0.10647965 0.09100565
  0.11095343 0.09769089 0.09863719 0.10277574]
 [0.10126188 0.10811083 0.09514029 0.09522072 0.10252064 0.09450807
  0.09819729 0.0993698  0.10187754 0.10379288]
 [0.10837164 0.09137017 0.09178799 0.09578544 0.08892766 0.10645469
  0.11150619 0.10478366 0.09968078 0.1

INFO:tensorflow:global_step/sec: 7.37086
INFO:tensorflow:probabilities = [[0.11688189 0.09267771 0.09188531 0.10279165 0.10473094 0.09690839
  0.10909606 0.08739474 0.10320982 0.09442341]
 [0.09583869 0.08619605 0.1017996  0.10811749 0.10163115 0.09004843
  0.11630883 0.10086102 0.10600223 0.09319641]
 [0.10388552 0.10148095 0.08976624 0.08793727 0.10475715 0.08904162
  0.11415344 0.10094304 0.10137425 0.10666058]
 [0.09397217 0.10619047 0.08644558 0.1090296  0.09056953 0.10039733
  0.106421   0.09375841 0.10423428 0.10898171]
 [0.10934798 0.10090113 0.09573177 0.09928736 0.08759446 0.10009921
  0.11264966 0.08793683 0.10278539 0.1036662 ]
 [0.09964765 0.10851601 0.08305296 0.09896749 0.10823597 0.09182877
  0.10939191 0.0956305  0.10197549 0.10275327]
 [0.09947531 0.11258015 0.09078363 0.0989081  0.08922718 0.09706601
  0.10461314 0.10011464 0.10463291 0.10259897]
 [0.09509737 0.10074024 0.08981906 0.09429953 0.09780567 0.10946871
  0.09934901 0.10124913 0.10771476 0.10445653]
 [0.094

...

INFO:tensorflow:global_step/sec: 6.9916
INFO:tensorflow:probabilities = [[0.00002326 0.0000038  0.00045583 0.01061573 0.00000081 0.98848176
  0.00001622 0.00000027 0.00022967 0.00017271]
 [0.00009248 0.00000702 0.0003162  0.00043713 0.00012277 0.00059339
  0.00008827 0.00000135 0.99820316 0.00013813]
 [0.00000085 0.00000601 0.00000351 0.00010207 0.9823346  0.00065661
  0.00000169 0.00756281 0.00156117 0.00777077]
 [0.00000006 0.00000433 0.0000068  0.00007538 0.00000686 0.00019464
  0.00000037 0.00000063 0.99967897 0.00003191]
 [0.00000015 0.00000147 0.00000433 0.00006127 0.00951759 0.00001539
  0.00000017 0.00105256 0.00011137 0.9892357 ]
 [0.98455334 0.00000035 0.00002892 0.00003378 0.00000026 0.01484577
  0.00002053 0.00040445 0.00000497 0.0001077 ]
 [0.00000002 0.00000037 0.9999356  0.00005736 0.00000001 0.00000007
  0.00000015 0.00000001 0.00000576 0.00000069]
 [0.0002706  0.00000215 0.00026936 0.03520411 0.00007346 0.1674897
  0.00000017 0.09828395 0.00230446 0.69610196]
 [0.00018

INFO:tensorflow:loss = 0.077911064, step = 19902 (14.305 sec)
INFO:tensorflow:probabilities = [[0.00000113 0.00000386 0.00000134 0.0000873  0.0585917  0.00001698
  0.00000393 0.00010228 0.0002135  0.940978  ]
 [0.00000051 0.00000545 0.00000043 0.00007138 0.01409053 0.00002179
  0.00000066 0.00150376 0.00000307 0.9843024 ]
 [0.19647141 0.00127931 0.01495773 0.02694175 0.01332728 0.06966135
  0.22470765 0.00043785 0.44706026 0.00515539]
 [0.00002271 0.00001931 0.00028291 0.00000902 0.00276411 0.00002168
  0.99685043 0.00000304 0.00002281 0.00000409]
 [0.0000128  0.985913   0.0015322  0.00049412 0.00001653 0.00010574
  0.00146087 0.00002711 0.01043321 0.00000439]
 [0.         0.         0.00000095 0.00000306 0.         0.
  0.         0.99999154 0.         0.00000445]
 [0.00000004 0.00000185 0.00029747 0.99944144 0.00000001 0.00002242
  0.00000001 0.00000001 0.00023659 0.0000001 ]
 [0.00004182 0.00000034 0.00130845 0.0125343  0.00000016 0.00126841
  0.00001472 0.00000202 0.98481303 0.0000

INFO:tensorflow:Saving checkpoints for 20001 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.123801515.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-28-19:57:36
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20001
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-28-19:57:41
INFO:tensorflow:Saving dict for global step 20001: accuracy = 0.9705, global_step = 20001, loss = 0.09799461
{'accuracy': 0.9705, 'loss': 0.09799461, 'global_step': 20001}


SystemExit: 

/home/dwhite54/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  # compilation of odd code (such as a naked 'return' outside a


mnist_with_summaries.py

In [3]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import argparse
import os
import sys

import tensorflow as tf

from tensorflow.examples.tutorials.mnist import input_data

FLAGS = None


def train():
    # Import data
    mnist = input_data.read_data_sets(FLAGS.data_dir, fake_data=FLAGS.fake_data)

    sess = tf.InteractiveSession()
    # Create a multilayer model.

    # Input placeholders
    with tf.name_scope('input'):
        x = tf.placeholder(tf.float32, [None, 784], name='x-input')
        y_ = tf.placeholder(tf.int64, [None], name='y-input')

    with tf.name_scope('input_reshape'):
        image_shaped_input = tf.reshape(x, [-1, 28, 28, 1])
        tf.summary.image('input', image_shaped_input, 10)

    # We can't initialize these variables to 0 - the network will get stuck.
    def weight_variable(shape):
        """Create a weight variable with appropriate initialization."""
        initial = tf.truncated_normal(shape, stddev=0.1)
        return tf.Variable(initial)

    def bias_variable(shape):
        """Create a bias variable with appropriate initialization."""
        initial = tf.constant(0.1, shape=shape)
        return tf.Variable(initial)

    def variable_summaries(var):
        """Attach a lot of summaries to a Tensor (for TensorBoard visualization)."""
        with tf.name_scope('summaries'):
            mean = tf.reduce_mean(var)
            tf.summary.scalar('mean', mean)
            with tf.name_scope('stddev'):
                stddev = tf.sqrt(tf.reduce_mean(tf.square(var - mean)))
            tf.summary.scalar('stddev', stddev)
            tf.summary.scalar('max', tf.reduce_max(var))
            tf.summary.scalar('min', tf.reduce_min(var))
            tf.summary.histogram('histogram', var)

    def nn_layer(input_tensor, input_dim, output_dim, layer_name, act=tf.nn.relu):
        """Reusable code for making a simple neural net layer.

        It does a matrix multiply, bias add, and then uses ReLU to nonlinearize.
        It also sets up name scoping so that the resultant graph is easy to read,
        and adds a number of summary ops.
        """
        # Adding a name scope ensures logical grouping of the layers in the graph.
        with tf.name_scope(layer_name):
            # This Variable will hold the state of the weights for the layer
            with tf.name_scope('weights'):
                weights = weight_variable([input_dim, output_dim])
                variable_summaries(weights)
            with tf.name_scope('biases'):
                biases = bias_variable([output_dim])
                variable_summaries(biases)
            with tf.name_scope('Wx_plus_b'):
                preactivate = tf.matmul(input_tensor, weights) + biases
                tf.summary.histogram('pre_activations', preactivate)
            activations = act(preactivate, name='activation')
            tf.summary.histogram('activations', activations)
            return activations

    hidden1 = nn_layer(x, 784, 500, 'layer1')

    with tf.name_scope('dropout'):
        keep_prob = tf.placeholder(tf.float32)
        tf.summary.scalar('dropout_keep_probability', keep_prob)
        dropped = tf.nn.dropout(hidden1, keep_prob)

    # Do not apply softmax activation yet, see below.
    y = nn_layer(dropped, 500, 10, 'layer2', act=tf.identity)

    with tf.name_scope('cross_entropy'):
        # The raw formulation of cross-entropy,
        #
        # tf.reduce_mean(-tf.reduce_sum(y_ * tf.log(tf.softmax(y)),
        #                                                             reduction_indices=[1]))
        #
        # can be numerically unstable.
        #
        # So here we use tf.losses.sparse_softmax_cross_entropy on the
        # raw logit outputs of the nn_layer above, and then average across
        # the batch.
        with tf.name_scope('total'):
            cross_entropy = tf.losses.sparse_softmax_cross_entropy(
                    labels=y_, logits=y)
    tf.summary.scalar('cross_entropy', cross_entropy)

    with tf.name_scope('train'):
        train_step = tf.train.AdamOptimizer(FLAGS.learning_rate).minimize(
                cross_entropy)

    with tf.name_scope('accuracy'):
        with tf.name_scope('correct_prediction'):
            correct_prediction = tf.equal(tf.argmax(y, 1), y_)
        with tf.name_scope('accuracy'):
            accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))
    tf.summary.scalar('accuracy', accuracy)

    # Merge all the summaries and write them out to
    # /tmp/tensorflow/mnist/logs/mnist_with_summaries (by default)
    merged = tf.summary.merge_all()
    train_writer = tf.summary.FileWriter(FLAGS.log_dir + '/train', sess.graph)
    test_writer = tf.summary.FileWriter(FLAGS.log_dir + '/test')
    tf.global_variables_initializer().run()

    # Train the model, and also write summaries.
    # Every 10th step, measure test-set accuracy, and write test summaries
    # All other steps, run train_step on training data, & add training summaries

    def feed_dict(train):
        """Make a TensorFlow feed_dict: maps data onto Tensor placeholders."""
        if train or FLAGS.fake_data:
            xs, ys = mnist.train.next_batch(100, fake_data=FLAGS.fake_data)
            k = FLAGS.dropout
        else:
            xs, ys = mnist.test.images, mnist.test.labels
            k = 1.0
        return {x: xs, y_: ys, keep_prob: k}

    for i in range(FLAGS.max_steps):
        if i % 10 == 0:    # Record summaries and test-set accuracy
            summary, acc = sess.run([merged, accuracy], feed_dict=feed_dict(False))
            test_writer.add_summary(summary, i)
            print('Accuracy at step %s: %s' % (i, acc))
        else:    # Record train set summaries, and train
            if i % 100 == 99:    # Record execution stats
                run_options = tf.RunOptions(trace_level=tf.RunOptions.FULL_TRACE)
                run_metadata = tf.RunMetadata()
                summary, _ = sess.run([merged, train_step],
                                                            feed_dict=feed_dict(True),
                                                            options=run_options,
                                                            run_metadata=run_metadata)
                train_writer.add_run_metadata(run_metadata, 'step%03d' % i)
                train_writer.add_summary(summary, i)
                print('Adding run metadata for', i)
            else:    # Record a summary
                summary, _ = sess.run([merged, train_step], feed_dict=feed_dict(True))
                train_writer.add_summary(summary, i)
    train_writer.close()
    test_writer.close()


def main(_):
    if tf.gfile.Exists(FLAGS.log_dir):
        tf.gfile.DeleteRecursively(FLAGS.log_dir)
    tf.gfile.MakeDirs(FLAGS.log_dir)
    train()


if __name__ == '__main__':
    parser = argparse.ArgumentParser()
    parser.add_argument('--fake_data', nargs='?', const=True, type=bool,
                                            default=False,
                                            help='If true, uses fake data for unit testing.')
    parser.add_argument('--max_steps', type=int, default=1000,
                                            help='Number of steps to run trainer.')
    parser.add_argument('--learning_rate', type=float, default=0.001,
                                            help='Initial learning rate')
    parser.add_argument('--dropout', type=float, default=0.9,
                                            help='Keep probability for training dropout.')
    parser.add_argument(
            '--data_dir',
            type=str,
            default=os.path.join(os.getenv('TEST_TMPDIR', '.'),
                                                     'tensorflow/mnist/input_data'),
            help='Directory for storing input data')
    parser.add_argument(
            '--log_dir',
            type=str,
            default=os.path.join(os.getenv('TEST_TMPDIR', '.'),
                                                     'tensorflow/mnist/logs/mnist_with_summaries'),
            help='Summaries log directory')
    FLAGS, unparsed = parser.parse_known_args()
    tf.app.run(main=main, argv=[sys.argv[0]] + unparsed)


Extracting /tmp/tensorflow/mnist/input_data/train-images-idx3-ubyte.gz
Extracting /tmp/tensorflow/mnist/input_data/train-labels-idx1-ubyte.gz
Extracting /tmp/tensorflow/mnist/input_data/t10k-images-idx3-ubyte.gz
Extracting /tmp/tensorflow/mnist/input_data/t10k-labels-idx1-ubyte.gz
Accuracy at step 0: 0.1358
Accuracy at step 10: 0.7261
Accuracy at step 20: 0.8313
Accuracy at step 30: 0.8707
Accuracy at step 40: 0.8823
Accuracy at step 50: 0.8925
Accuracy at step 60: 0.8977
Accuracy at step 70: 0.9006
Accuracy at step 80: 0.8916
Accuracy at step 90: 0.9073
Adding run metadata for 99
Accuracy at step 100: 0.9175
Accuracy at step 110: 0.9217
Accuracy at step 120: 0.9247
Accuracy at step 130: 0.9247
Accuracy at step 140: 0.9286
Accuracy at step 150: 0.9299
Accuracy at step 160: 0.9301
Accuracy at step 170: 0.9291
Accuracy at step 180: 0.9326
Accuracy at step 190: 0.9341
Adding run metadata for 199
Accuracy at step 200: 0.9324
Accuracy at step 210: 0.9374
Accuracy at step 220: 0.9369
Accurac

SystemExit: 

/home/dwhite54/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  # compilation of odd code (such as a naked 'return' outside a
